# Анализ пространственных данных. Домашнее задание №2

Мягкий дедлайн: __4 ноября 2020 г. 23:59__

Жесткий дедлайн (со штрафом в _50%_ от количества набранных вами за ДЗ баллов): __5 ноября 2020 г. 08:59__

Визуализация "чего-либо" __без__ выполненного основного задания оценивается в __0 баллов__

ФИО: `Миневич Павел`

Группа: `DS-11`

## Задание №1. Горячая точка (алгоритм - 10 баллов, визуализация - 10 баллов).

Генерируйте рандомные точки на планете Земля до тех пор, пока не попадете на территорию ``Афганистана``

1. Вы можете использовать функции принадлжености точки полигону и расстояния от точки до полигона (в метрах)
2. Предложите не наивный алгоритм поиска (генерировать __напрямую__ точку из полигона границ Афганистана __запрещено__)

In [2]:
import os 
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from matplotlib.ticker import ScalarFormatter
import seaborn as sns
import geopandas as gpd
from shapely.geometry import Point, LineString, Polygon, MultiPolygon
from shapely import wkt, geometry
import earthpy as et 
import folium
import random
import pyproj
import shapely.wkb
from openrouteservice import client

In [3]:
#Для определения границ загрузил данные отсюда 
#http://www.naturalearthdata.com/downloads/110m-cultural-vectors/110m-admin-0-countries/
borders_df = gpd.read_file('/home/karv/DS/MADE/Geo/HW2/ne_110m_admin_0_countries.shp')
afg_border = borders_df[borders_df['ADM0_A3'] == 'AFG'].geometry.values[0]
coord_string = afg_border.to_wkt()[10:-2]
coord_list = [(float(x.strip().split(' ')[1]), float(x.strip().split(' ')[0])) for x in coord_string.split(',')]

m = folium.Map(location=[0, 0], zoom_start=2)
folium.Polygon(coord_list).add_to(m)
m

In [4]:
# Алгоритм выбирает, какой из 4-х квадрантов содержит страну.
delta = 0.001
top = 89
bottom = -89
left = -180
right = 180

points = []

point_found = False
while not point_found:
    long = random.random() * (right - left) + left
    lat = random.random() * (top - bottom) + bottom
#     print(long, lat)
    points.append((long, lat))
    if afg_border.contains(Point(points[-1])):
        point_found = True
        break
        
    d1 = afg_border.distance(Point(points[-1][0] + delta, points[-1][1] + delta))
    d2 = afg_border.distance(Point(points[-1][0] - delta, points[-1][1] + delta))
    d3 = afg_border.distance(Point(points[-1][0] + delta, points[-1][1] - delta))
    d4 = afg_border.distance(Point(points[-1][0] - delta, points[-1][1] - delta))
    
    if d1 <= d2 and d1 <= d3 and d1 <= d4:
        bottom = lat
        left = long
    elif d2 <= d1 and d2 <= d3 and d2 <= d4:
        bottom = lat
        right = long
    elif d3 <= d1 and d3 <= d2 and d3 <= d4:
        top = lat
        left = long
    else:
        top = lat
        right = long

In [5]:
for i in range(1, len(points)):
    folium.Polygon([(points[i][1], points[i][0]), (points[i - 1][1], points[i - 1][0])], popup=str(i)).add_to(m)
    
m

Визуализируйте пошагово предложенный алгоритм при помощи ``Folium``

## Задание №2. Качество жизни (20 баллов).

Для измерения показателя качества жизни в точке, найденной в предыдущем задании, вам необходимо рассчитать следующую сумму расстояний (в метрах):

1. Расстояние от точки до 5 ближайших __*__ банкоматов, находящихся в стране с наибольшим количеством объектов жилой недвижимости
2. Расстояние от точки до 5 ближайших школ, находящихся в стране с наибольшим количеством аптек в столице
3. Расстояние от точки до 5 ближайших кинотеатров, наодящихся в стране с самым большим отношением числа железнодорожных станций к автобусным остановкам в южной части __**__

__*__ При поиске _N_ ближайших объектов обязательно использовать ``R-tree``

__**__ Южной частью страны является территория, находящаяся к югу от множества точек, равноудаленных от самой северной и самой южной точек страны

In [ ]:
# put your code here

## Задание №3. Поездка по Нью-Йорку (маршрут - 20 баллов, визуализация - 10 баллов).

Добраться __на автомобиле__ от входа в ``Central Park`` __Нью-Йорка__ (со стороны ``5th Avenue``) до пересечения ``Water Street`` и ``Washington Street`` в Бруклине (откуда получаются лучшие фото Манхэттенского моста) довольно непросто - разумеется, из-за вечных пробок. Однако еще сложнее это сделать, проезжая мимо школ, где дети то и дело переходят дорогу в неположенном месте.

Вам необходимо построить описанный выше маршрут, избегая на своем пути школы. Визуализируйте данный маршрут (также добавив школы и недоступные для проезда участки дорог) при помощи ``Folium``

Данные о расположении школ Нью-Йорка можно найти [здесь](https://catalog.data.gov/dataset/2019-2020-school-point-locations)

In [6]:
def str_to_point(string):
    long, lat = [float(x.strip('()')) for x in string.split(' ')[1:]]
    Point(long, lat)
    return Point

In [7]:
df = pd.read_csv('2019_-_2020_School_Point_Locations.csv')
df.the_geom = df.the_geom.apply(wkt.loads)
df.head()

the_geom ATS_Code Loc_Code  \
0  POINT (-73.85554326311143 40.70843092338607)   75Q233     Q233   
1  POINT (-73.98866531387878 40.76132731795493)   02M212     M212   
2  POINT (-73.73770240439862 40.71098671281902)   29Q034     Q034   
3  POINT (-73.94070782764723 40.66180674321865)   17K091     K091   
4  POINT (-74.19343130285691 40.52815208490681)   31R455     R455   

                            Loc_Name  Managed_by  LCC PrimaryBui      BIN  \
0                          P.S. Q233           1    7       Q686  4447233   
1              P.S. 212 Midtown West           1    2       M017  1025092   
2              P.S. 034 John Harvard           1    2       Q034  4240503   
3  P.S. 091 The Albany Avenue School           1    2       K091  3106599   
4            Tottenville High School           1    5       R455  5082634   

            BBL                       Address           City  BoroNum State  \
0  4.038861e+09     91-30 METROPOLITAN AVENUE         QUEENS        4    NY   
1  1.010380e+09           328 WEST  48 STREET      MANHATTAN        1    NY   
2  4.111510e+09  104-12 SPRINGFIELD BOULEVARD         QUEENS        4    NY   
3  3.047940e+09             532 ALBANY AVENUE       BROOKLYN        3    NY   
4  5.066130e+09              100 LUTEN AVENUE  STATEN ISLAND        5    NY   

     Zip  GeoDistric  AdiminDist  XCoordinat  YCoordinat  
0  11375          28          75     1024300      197410  
1  10036           2           2      987390      216649  
2  11429          29          29     1056968      198417  
3  11203          17          17     1000700      180396  
4  10312          31          31      930477      131756

In [19]:
gdf = gpd.GeoDataFrame(df, geometry='the_geom')
gdf.crs = "EPSG:4326"
gdf.head()

the_geom ATS_Code Loc_Code  \
0  POINT (-73.85554 40.70843)   75Q233     Q233   
1  POINT (-73.98867 40.76133)   02M212     M212   
2  POINT (-73.73770 40.71099)   29Q034     Q034   
3  POINT (-73.94071 40.66181)   17K091     K091   
4  POINT (-74.19343 40.52815)   31R455     R455   

                            Loc_Name  Managed_by  LCC PrimaryBui      BIN  \
0                          P.S. Q233           1    7       Q686  4447233   
1              P.S. 212 Midtown West           1    2       M017  1025092   
2              P.S. 034 John Harvard           1    2       Q034  4240503   
3  P.S. 091 The Albany Avenue School           1    2       K091  3106599   
4            Tottenville High School           1    5       R455  5082634   

            BBL                       Address           City  BoroNum State  \
0  4.038861e+09     91-30 METROPOLITAN AVENUE         QUEENS        4    NY   
1  1.010380e+09           328 WEST  48 STREET      MANHATTAN        1    NY   
2  4.111510e+09  104-12 SPRINGFIELD BOULEVARD         QUEENS        4    NY   
3  3.047940e+09             532 ALBANY AVENUE       BROOKLYN        3    NY   
4  5.066130e+09              100 LUTEN AVENUE  STATEN ISLAND        5    NY   

     Zip  GeoDistric  AdiminDist  XCoordinat  YCoordinat  
0  11375          28          75     1024300      197410  
1  10036           2           2      987390      216649  
2  11429          29          29     1056968      198417  
3  11203          17          17     1000700      180396  
4  10312          31          31      930477      131756

In [22]:
#Looking for wrong point
gdf.drop(gdf[gdf['YCoordinat'] < 50].index, inplace=True)

In [23]:
#Plotting on map - works long fo 2000 points, for demo plot just 50:100
start_point = [gdf.the_geom[0].coords[0][1], gdf.the_geom[0].coords[0][0]]
m = folium.Map(location=start_point, zoom_start=10)
for school in gdf.the_geom[50:100]:
    folium.Marker([school.coords[0][1], school.coords[0][0]]).add_to(m)
# folium.Polygon(coord_list).add_to(m)
m

In [63]:
route_start = [-73.96722, 40.77248] #Starting point
route_end = [-73.98958, 40.70319 ] #end point
avoid_radius = 0.001


In [64]:
def create_buffer_polygon(point_in, resolution=10, radius=10):    

    point_in_proj = point_in
    point_buffer_proj = Point(point_in_proj).buffer(radius, resolution=resolution)
    
    # Iterate over all points in buffer and build polygon
    poly_wgs = []
    for point in point_buffer_proj.exterior.coords:
        poly_wgs.append(point)

    return poly_wgs

In [65]:
map_params = {'tiles':'Stamen Toner',
              'location':list(reversed(route_start)),
              'zoom_start': 12}#,
#               'crs': 'EPSG4326'}
map1 = folium.Map(**map_params)

# Populate a construction site buffer polygon list
schools_poly = []
for school in gdf.the_geom:
    school_coords = school.coords[0]
    folium.features.Marker(list(reversed(school_coords)),
                           popup='School<br>{0}'.format(school_coords)).add_to(map1)
    
    # Create buffer polygons around construction sites with 10 m radius and low resolution
    school_poly_coords = create_buffer_polygon(school_coords,
                                           resolution=2, # low resolution to keep polygons lean
                                           radius=avoid_radius)
    schools_poly.append(school_poly_coords)
    
    
    school_poly_coords = [(y,x) for x,y in school_poly_coords] # Reverse coords for folium/Leaflet
    folium.vector_layers.Polygon(locations=school_poly_coords,
                                  color='#ffd699',
                                  fill_color='#ffd699',
                                  fill_opacity=0.2,
                                  weight=3).add_to(map1)
    
map1

In [66]:
# GeoJSON style function
def style_function(color):
    return lambda feature: dict(color=color,
                              weight=3,
                              opacity=0.5)

# Set up the fundamentals
api_key = '5b3ce3597851110001cf6248d02e6c4b59b245628cde0cfcf7b496ec' # Individual api key
clnt = client.Client(key=api_key) # Create client with api key

map_params = {'tiles':'Stamen Toner',
              'location':list(reversed(route_start)),
              'zoom_start': 12,
              
             }

map2 = folium.Map(**map_params)
request_params = {'coordinates': [route_start, route_end],
                  'format_out': 'geojson',
                  'profile': 'driving-car',
                  'preference': 'shortest',
                  'instructions': 'false'
                 }

route_normal = clnt.directions(**request_params)
folium.features.GeoJson(data=route_normal,
                        name='Route without construction sites',
                        style_function=style_function('#FF0000'),
                        overlay=True).add_to(map2)

route_buffer = LineString(route_normal['features'][0]['geometry']['coordinates']).buffer(0.1)
folium.features.GeoJson(data=geometry.mapping(route_buffer),
                        name='Route Buffer',
                        style_function=style_function('#FFFF00'),
                        overlay=True).add_to(map2)

# Plot which construction sites fall into the buffer Polygon
schools_buffer_poly = []
for school_poly in schools_poly:
    poly = Polygon(school_poly)
    if route_buffer.intersects(poly):
        folium.features.Marker(list(reversed(poly.centroid.coords[0]))).add_to(map2)
        schools_buffer_poly.append(poly)
        folium.Polygon(locations=[(y,x) for x,y in school_poly],
                                  color='#ffd699',
                                  fill_color='#ffd699',
                                  fill_opacity=0.2,
                                  weight=3).add_to(map2)


In [67]:
map2

In [68]:
# Add the site polygons to the request parameters
request_params['options'] = {'avoid_polygons': geometry.mapping(MultiPolygon(schools_buffer_poly))}
route_detour = clnt.directions(**request_params)

folium.features.GeoJson(data=route_detour,
                        name='Route with construction sites',
                        style_function=style_function('#00FF00'),
                        overlay=True).add_to(map2)

map2.add_child(folium.map.LayerControl())
map2